In [1]:
import pandas as pd
import numpy as np

In [2]:
data=pd.read_csv('../00_DATA/final_dataset.csv')

In [3]:
data['startYear']=data['startYear'].astype(int)
data

tconst                                       primaryTitle  \
0       tt0035423                                     Kate & Leopold   
1       tt0036177                                 Muhomatsu no issho   
2       tt0062336  The Tango of the Widower and Its Distorting Mi...   
3       tt0065392                                 Bucharest Memories   
4       tt0069049                         The Other Side of the Wind   
...           ...                                                ...   
147377  tt9915872                               The Last White Witch   
147378  tt9916170                                      The Rehearsal   
147379  tt9916190                                          Safeguard   
147380  tt9916362                                              Coven   
147381  tt9916428                                The Secret of China   

                                    originalTitle  isAdult  startYear  \
0                                  Kate & Leopold        0       2001   
1                              Muhomatsu no issho        0       2008   
2       El Tango del Viudo y Su Espejo Deformante        0       2020   
3                            Amintiri bucurestene        0       2020   
4                      The Other Side of the Wind        0       2018   
...                                           ...      ...        ...   
147377                  My Girlfriend is a Wizard        0       2019   
147378                                   O Ensaio        0       2019   
147379                                  Safeguard        0       2020   
147380                                   Akelarre        0       2020   
147381               Hong xing zhao yao Zhong guo        0       2019   

       runtimeMinutes  Adult  Animation  Fantasy  Game-Show  ...  News  \
0                 118      0          0        1          0  ...     0   
1                 100      0          0        0          0  ...     0   
2                  70      0          0        0          0  ...     0   
3                  \N      0          0        0          0  ...     0   
4                 122      0          0        0          0  ...     0   
...               ...    ...        ...      ...        ...  ...   ...   
147377             97      0          0        1          0  ...     0   
147378             51      0          0        0          0  ...     0   
147379             90      0          0        0          0  ...     0   
147380             92      0          0        0          0  ...     0   
147381             \N      0          0        0          0  ...     0   

        Reality-TV  Sci-Fi  Short  Sport  Talk-Show  War  Western  \
0                0       0      0      0          0    0        0   
1                0       0      0      0          0    0        0   
2                0       0      0      0          0    0        0   
3                0       0      0      0          0    0        0   
4                0       0      0      0          0    0        0   
...            ...     ...    ...    ...        ...  ...      ...   
147377           0       0      0      0          0    0        0   
147378           0       0      0      0          0    0        0   
147379           0       0      0      0          0    0        0   
147380           0       0      0      0          0    0        0   
147381           0       0      0      0          0    1        0   

        averageRating  numVotes  
0                 6.4   81936.0  
1                 7.3     113.0  
2                 6.3     157.0  
3                 7.4      12.0  
4                 6.8    6930.0  
...               ...       ...  
147377            7.7       7.0  
147378            7.2       5.0  
147379            3.6     226.0  
147380            6.4    4085.0  
147381            3.8      14.0  

[147382 rows x 23 columns]

In [4]:
# keeping titles from 2000 and above only
data = data[data['startYear'] >= 2000]
titles = data['primaryTitle']
titles

0                                            Kate & Leopold
1                                        Muhomatsu no issho
2         The Tango of the Widower and Its Distorting Mi...
3                                        Bucharest Memories
4                                The Other Side of the Wind
                                ...                        
147377                                 The Last White Witch
147378                                        The Rehearsal
147379                                            Safeguard
147380                                                Coven
147381                                  The Secret of China
Name: primaryTitle, Length: 131682, dtype: object

In [5]:
# how many movies after 2000 are there?
len(titles)

131682

# Practice Run - no need to run this cell

In [2]:
# PRACTICE API CALL FOR ONE HARDCODED MOVIE: "THE DARK KNIGHT"
import tmdbsimple as tmdb

# Clem's API key
tmdb.API_KEY = 'f6553225b3b37ae2a29dad9a832393d9'

# In case clem's doesn't work, you can use mine (louis)
# tmdb.API_KEY = 'ae28396bb24c53a5d6b8a64a0ac95bf8'

search = tmdb.Search()

# First request to get the movie's IMDB id based on its title
response1 = search.movie(query="The Dark Knight")
movie_id = response1['results'][0]['id']

# Second request to get all the information about the movie using the id
movie = tmdb.Movies(movie_id)
movie_info = movie.info()

# The information we need to save for the project:
budget = movie_info['budget']
revenue = movie_info['revenue']
movie_id # so we can easily re-access the API if needed

{'adult': False,
 'backdrop_path': '/nMKdUUepR0i5zn0y1T4CsSB5chy.jpg',
 'belongs_to_collection': {'id': 263,
  'name': 'The Dark Knight Collection',
  'poster_path': '/l4T8JVwircGZlZuSl29U3TS9mpl.jpg',
  'backdrop_path': '/xfKot7lqaiW4XpL5TtDlVBA9ei9.jpg'},
 'budget': 185000000,
 'genres': [{'id': 18, 'name': 'Drama'},
  {'id': 28, 'name': 'Action'},
  {'id': 80, 'name': 'Crime'},
  {'id': 53, 'name': 'Thriller'}],
 'homepage': 'https://www.warnerbros.com/movies/dark-knight/',
 'id': 155,
 'imdb_id': 'tt0468569',
 'original_language': 'en',
 'original_title': 'The Dark Knight',
 'overview': 'Batman raises the stakes in his war on crime. With the help of Lt. Jim Gordon and District Attorney Harvey Dent, Batman sets out to dismantle the remaining criminal organizations that plague the streets. The partnership proves to be effective, but they soon find themselves prey to a reign of chaos unleashed by a rising criminal mastermind known to the terrified citizens of Gotham as the Joker.',
 '

# Real loop

Includes:
- a try/except structure to avoid the code to crash if the movie id is not found
- a safety backup to CSV every 1000 movie, just in case
- stores the IMDB id, movie title (for visual clue), budget, and revenue
- If the stored revenue is 0, it is not published on IMDB
- If the stored revenue is -1, the movie was not found on IMDB

In [6]:
# FULL LOOP - THIS IS THE IMPORTANT CELL! 

api_results = []

import tmdbsimple as tmdb
tmdb.API_KEY = 'f6553225b3b37ae2a29dad9a832393d9'
search = tmdb.Search()

for index, movie_title in enumerate(titles[:]): # for a test run, replace this line by: for movie_title in titles[0:50]
    
    print("Fetching movie number", index + 1, "out of", len(titles), '...')
    response = search.movie(query=movie_title)
    
    try:
        movie_id = response['results'][0]['id']
        movie = tmdb.Movies(movie_id)
        movie_info = movie.info()
        budget = movie_info['budget']
        revenue = movie_info['revenue']
        
        print("Title:", movie_title)
        print("Budget:", budget)
        print("Revenue:", revenue)
        
    except:
        movie_id, budget, revenue = -1, -1, -1
        print("movie not found in API")
        
    
    # saving results to the api_results dataframe:
    api_results.append({'title': movie_title, 'imdb_id': movie_id, 'budget': budget, 'revenue': revenue})
    
    # saves the data to a CSV every "save_frequency". Feel free to change the value
    save_frequency = 10000
    if (index + 1) % save_frequency == 0:
        save_df = pd.DataFrame(api_results)
        save_df.to_csv('api_backup_v2.csv')
        print("***Current movies saved to a CSV.***")
    
    print("\n")


Fetching movie number 1 out of 131682 ...
Title: Kate & Leopold
Budget: 48000000
Revenue: 76019048


Fetching movie number 2 out of 131682 ...
Title: Muhomatsu no issho
Budget: 0
Revenue: 0


Fetching movie number 3 out of 131682 ...
Title: The Tango of the Widower and Its Distorting Mirror
Budget: 0
Revenue: 0


Fetching movie number 4 out of 131682 ...
Title: Bucharest Memories
Budget: 0
Revenue: 0


Fetching movie number 5 out of 131682 ...
Title: The Other Side of the Wind
Budget: 12000000
Revenue: 0


Fetching movie number 6 out of 131682 ...
Title: The Naked Monster
Budget: 350000
Revenue: 0


Fetching movie number 7 out of 131682 ...
Title: Grizzly II: Revenge
Budget: 7500000
Revenue: 0


Fetching movie number 8 out of 131682 ...
Title: Crime and Punishment
Budget: 0
Revenue: 0


Fetching movie number 9 out of 131682 ...
Title: The Wandering Soap Opera
Budget: 0
Revenue: 0


Fetching movie number 10 out of 131682 ...
movie not found in API


Fetching movie number 11 out of 13168

Title: Dinosaur
Budget: 127500000
Revenue: 354248063


Fetching movie number 91 out of 131682 ...
Title: Split
Budget: 9000000
Revenue: 278454358


Fetching movie number 92 out of 131682 ...
Title: The Adventures of Rocky & Bullwinkle
Budget: 76000000
Revenue: 35134820


Fetching movie number 93 out of 131682 ...
Title: Dead by Monday
Budget: 0
Revenue: 0


Fetching movie number 94 out of 131682 ...
Title: Driven
Budget: 94000000
Revenue: 54744738


Fetching movie number 95 out of 131682 ...
Title: BlackMale
Budget: 0
Revenue: 0


Fetching movie number 96 out of 131682 ...
Title: The Crow: Salvation
Budget: 10000000
Revenue: 0


Fetching movie number 97 out of 131682 ...
Title: Lightmaker
Budget: 0
Revenue: 0


Fetching movie number 98 out of 131682 ...
Title: Planet of the Apes
Budget: 170000000
Revenue: 710644566


Fetching movie number 99 out of 131682 ...
Title: Treasure Planet
Budget: 140000000
Revenue: 109578115


Fetching movie number 100 out of 131682 ...
Title: Fallen Arches
B

Title: Up at the Villa
Budget: 0
Revenue: 0


Fetching movie number 181 out of 131682 ...
movie not found in API


Fetching movie number 182 out of 131682 ...
Title: Jackpot
Budget: 0
Revenue: 0


Fetching movie number 183 out of 131682 ...
Title: Bitten: Victoria's Shadow
Budget: 0
Revenue: 0


Fetching movie number 184 out of 131682 ...
Title: Wild Blue
Budget: 0
Revenue: 0


Fetching movie number 185 out of 131682 ...
Title: The Bacchae
Budget: 0
Revenue: 0


Fetching movie number 186 out of 131682 ...
Title: Condo Painting
Budget: 0
Revenue: 0


Fetching movie number 187 out of 131682 ...
Title: Home Movies
Budget: 0
Revenue: 0


Fetching movie number 188 out of 131682 ...
Title: Secrets of a Chambermaid
Budget: 0
Revenue: 0


Fetching movie number 189 out of 131682 ...
Title: A Good Baby
Budget: 0
Revenue: 0


Fetching movie number 190 out of 131682 ...
Title: I'll Remember April
Budget: 1800000
Revenue: 0


Fetching movie number 191 out of 131682 ...
Title: Ricky 6
Budget: 0
Reve

Title: Unseen Evil
Budget: 0
Revenue: 0


Fetching movie number 272 out of 131682 ...
Title: Blue Shark Hash
Budget: 0
Revenue: 0


Fetching movie number 273 out of 131682 ...
Title: Cast Away
Budget: 90000000
Revenue: 429632142


Fetching movie number 274 out of 131682 ...
Title: Ghost World
Budget: 7000000
Revenue: 0


Fetching movie number 275 out of 131682 ...
Title: Shaft
Budget: 30000000
Revenue: 21360215


Fetching movie number 276 out of 131682 ...
Title: Stained Glass
Budget: 0
Revenue: 0


Fetching movie number 277 out of 131682 ...
Title: Trixie
Budget: 0
Revenue: 0


Fetching movie number 278 out of 131682 ...
Title: Three Days of Rain
Budget: 3500000
Revenue: 0


Fetching movie number 279 out of 131682 ...
Title: Hanging Up
Budget: 60000000
Revenue: 51880044


Fetching movie number 280 out of 131682 ...
Title: Jurassic Park III
Budget: 93000000
Revenue: 368780809


Fetching movie number 281 out of 131682 ...
Title: The Magic Pudding
Budget: 0
Revenue: 0


Fetching movie nu

Title: Peroxide Passion
Budget: 0
Revenue: 0


Fetching movie number 361 out of 131682 ...
Title: Prince of Central Park
Budget: 0
Revenue: 0


Fetching movie number 362 out of 131682 ...
Title: Il resto di niente
Budget: 0
Revenue: 0


Fetching movie number 363 out of 131682 ...
Title: TGM the Liberator
Budget: 0
Revenue: 0


Fetching movie number 364 out of 131682 ...
Title: Tigerland
Budget: 10000000
Revenue: 148701


Fetching movie number 365 out of 131682 ...
Title: Generation Ax
Budget: 0
Revenue: 0


Fetching movie number 366 out of 131682 ...
Title: Gun Shy
Budget: 0
Revenue: 0


Fetching movie number 367 out of 131682 ...
Title: Hamlet
Budget: 0
Revenue: 0


Fetching movie number 368 out of 131682 ...
Title: Keeping the Faith
Budget: 30000000
Revenue: 59945183


Fetching movie number 369 out of 131682 ...
movie not found in API


Fetching movie number 370 out of 131682 ...
Title: Nurse Betty
Budget: 24000000
Revenue: 0


Fetching movie number 371 out of 131682 ...
movie not fo

...

Title: The Deep Blue Sea
Budget: 0
Revenue: 1126525


Fetching movie number 56821 out of 131682 ...
Title: The Invisible Woman
Budget: 0
Revenue: 1234254


Fetching movie number 56822 out of 131682 ...
Title: The Girl in the Mirror
Budget: 0
Revenue: 0


Fetching movie number 56823 out of 131682 ...
movie not found in API


Fetching movie number 56824 out of 131682 ...
Title: Tungsten
Budget: 0
Revenue: 0


Fetching movie number 56825 out of 131682 ...
Title: Ultimate Reality
Budget: 0
Revenue: 0


Fetching movie number 56826 out of 131682 ...
Title: 1 Message
Budget: 0
Revenue: 0


Fetching movie number 56827 out of 131682 ...
movie not found in API


Fetching movie number 56828 out of 131682 ...
Title: Day of the Falcon
Budget: 40000000
Revenue: 5446000


Fetching movie number 56829 out of 131682 ...
Title: Dogs Lie
Budget: 0
Revenue: 0


Fetching movie number 56830 out of 131682 ...
Title: Future Weather
Budget: 0
Revenue: 0


Fetching movie number 56831 out of 131682 ...
Title: Hol

Title: Parasitic
Budget: 0
Revenue: 0


Fetching movie number 56913 out of 131682 ...
movie not found in API


Fetching movie number 56914 out of 131682 ...
movie not found in API


Fetching movie number 56915 out of 131682 ...
movie not found in API


Fetching movie number 56916 out of 131682 ...
Title: Road Dogs
Budget: 0
Revenue: 0


Fetching movie number 56917 out of 131682 ...
Title: Somewhere in Between
Budget: 0
Revenue: 0


Fetching movie number 56918 out of 131682 ...
movie not found in API


Fetching movie number 56919 out of 131682 ...
Title: Bernie
Budget: 5000000
Revenue: 9206470


Fetching movie number 56920 out of 131682 ...
Title: Consinsual
Budget: 0
Revenue: 0


Fetching movie number 56921 out of 131682 ...
Title: From the Rough
Budget: 0
Revenue: 0


Fetching movie number 56922 out of 131682 ...
Title: Lycanthrope
Budget: 0
Revenue: 0


Fetching movie number 56923 out of 131682 ...
Title: Tabloid
Budget: 0
Revenue: 0


Fetching movie number 56924 out of 131682 ...
Ti

Title: Charlie Don't Surf
Budget: 0
Revenue: 0


Fetching movie number 57003 out of 131682 ...
movie not found in API


Fetching movie number 57004 out of 131682 ...
Title: In the Future
Budget: 0
Revenue: 0


Fetching movie number 57005 out of 131682 ...
Title: Curse of the Deserted
Budget: 0
Revenue: 0


Fetching movie number 57006 out of 131682 ...
Title: Aakrosh
Budget: 0
Revenue: 0


Fetching movie number 57007 out of 131682 ...
Title: Fell
Budget: 14000000
Revenue: 19000000


Fetching movie number 57008 out of 131682 ...
Title: Oppai Chanbara: Striptease Samurai Squad
Budget: 0
Revenue: 0


Fetching movie number 57009 out of 131682 ...
Title: Snake Charmer
Budget: 10000
Revenue: 0


Fetching movie number 57010 out of 131682 ...
movie not found in API


Fetching movie number 57011 out of 131682 ...
movie not found in API


Fetching movie number 57012 out of 131682 ...
Title: Ready
Budget: 175000000
Revenue: 582890172


Fetching movie number 57013 out of 131682 ...
Title: The Drago

Title: 11-11-11
Budget: 0
Revenue: 0


Fetching movie number 57094 out of 131682 ...
Title: Alex Cross
Budget: 45000000
Revenue: 30353232


Fetching movie number 57095 out of 131682 ...
Title: High Chicago
Budget: 0
Revenue: 0


Fetching movie number 57096 out of 131682 ...
Title: The Ages of Love
Budget: 0
Revenue: 0


Fetching movie number 57097 out of 131682 ...
Title: Memphis the Musical
Budget: 0
Revenue: 0


Fetching movie number 57098 out of 131682 ...
Title: Message from the King
Budget: 10000000
Revenue: 0


Fetching movie number 57099 out of 131682 ...
movie not found in API


Fetching movie number 57100 out of 131682 ...
Title: Out of Europe
Budget: 0
Revenue: 0


Fetching movie number 57101 out of 131682 ...
Title: Out of Focus
Budget: 0
Revenue: 0


Fetching movie number 57102 out of 131682 ...
Title: Palace of Silents
Budget: 0
Revenue: 0


Fetching movie number 57103 out of 131682 ...
Title: Revenants
Budget: 0
Revenue: 0


Fetching movie number 57104 out of 131682 ...
T

ConnectionError: HTTPSConnectionPool(host='api.themoviedb.org', port=443): Max retries exceeded with url: /3/search/movie?query=Anna&api_key=f6553225b3b37ae2a29dad9a832393d9 (Caused by NewConnectionError('<urllib3.connection.HTTPSConnection object at 0x1314fb100>: Failed to establish a new connection: [Errno 50] Network is down'))

In [26]:
# If the loop finishes, you can inspect the full output here:

# print(api_results)




# or here:

# output = pd.DataFrame(api_results)




# if the loop fully worked, make sure to save it one last time to CSV:

# output = pd.DataFrame(api_results)
# output.to_csv('api_backup.csv')

                                               title  imdb_id    budget  \
0                                     Kate & Leopold    11232  48000000   
1                                 Muhomatsu no issho   895979         0   
2  The Tango of the Widower and Its Distorting Mi...   602986         0   
3                                 Bucharest Memories   741942         0   
4                         The Other Side of the Wind   299782  12000000   
5                                  The Naked Monster    29163    350000   
6                                Grizzly II: Revenge    38258   7500000   
7                               Crime and Punishment   109809         0   
8                           The Wandering Soap Opera   467254         0   
9                         West from North Goes South       -1        -1   

    revenue  
0  76019048  
1         0  
2         0  
3         0  
4         0  
5         0  
6         0  
7         0  
8         0  
9        -1  
